# LLM Abliterate v1.4 script, adapted for Mistral-Small-Instruct-2409

Author: byroneverson

This script ran at kaggle.com, accelerator: None, persistence: Files only

# Download quantized model locally

Downloading to /kaggle/temp dir so will need to keep the session open to keep model local

In [ ]:
%cd /kaggle/working

from huggingface_hub import hf_hub_download

hf_hub_download(repo_id="bartowski/Mistral-Small-Instruct-2409-GGUF", filename="Mistral-Small-Instruct-2409-Q4_K_M.gguf", local_dir="/kaggle/temp")

# Temporary: We need my fork of ggml-python because the official abetlen is out of date and ggml_tensor is incompatible at the moment.

In [ ]:
%cd /kaggle/working
!git clone --recurse-submodules https://github.com/byroneverson/ggml-python.git

# Install my ggml-python, llama-cpp-python, and couple other reqs

Using CUDA with llama.cpp for these larger models, you can install the normal llama-cpp-python if you want CPU only

In [ ]:
%cd /kaggle/working

!pip install ./ggml-python
!pip install llama-cpp-python --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cu123 #CUDA
#!pip install llama-cpp-python
!pip install jaxtyping
!pip install einops

# Obtain layer output embeddings for each of our sample instruction sets (harmful and harmless)

- These will be saved to the folders "harmful_states" and "harmless_states".
- Each output file contains a tensor of shape (n_layers * 2 + 1, n_embd).
- Output files will contain embeds for the token embeddings, and both the attn output and ffn output embeds of each layer.
- A quant model is used for this process with llama.cpp for minimal cpu and memory usage.
- This version of the script uses CUDA to split the layers workload between CPU and GPU.
- Start with too many GPU layers and decrease until you no longer have allocate errors to use as many GPU layers as possible.
- Considering we will end up using the mean of these samples, the amount of quantization shouldn't matter much.

In [ ]:
%cd /kaggle/working

import ctypes
import os
import multiprocessing
import random
import gc
import sys
import re
import llama_cpp
import ggml
import torch
from math import prod
from datasets import load_dataset
from tqdm import tqdm

# Number of total layers in your model
n_layers = 56
# GPU layers, use as many as possible, ideally all the layers and also the input embedding
n_gpu_layers = n_layers + 1 #0 # CPU only

# Number of instructions to average for our feature estimation (e.g. 512 for harmful and 512 for harmless)
instructions = 512 #256 #32

# Our local gguf model
# TODO: Load model with only num_layers we actually need for this step
working_dir = "/kaggle/working"
local_repo_dir = "/kaggle/temp"
model_path = local_repo_dir + "/" + "Mistral-Small-Instruct-2409-Q4_K_M.gguf"
chat_template = ctypes.c_char_p("mistral".encode("utf-8")) #None

# Init llama backend
llama_cpp.llama_backend_init(numa=False)

# llama.cpp custom model code

def c_array_to_tensor(pointer, shape, torch_type):
    arr = (pointer._type_ * prod(shape)).from_address(
    ctypes.addressof(pointer.contents))
    return torch.frombuffer(arr, dtype=torch_type).view(*shape)

def model_load(model_path):
    # TODO: Attempt to hook num_layers
    model_params = llama_cpp.llama_model_default_params()
    model_params.n_gpu_layers = n_gpu_layers
    model_params.use_mmap = True
    model = llama_cpp.llama_load_model_from_file(model_path.encode("utf-8"), model_params)
    return model

def model_free(model):
    llama_cpp.llama_free(model)
    
def model_tokenize_chat(model, role, content, add_assistant=True):
    role = role.encode("utf-8")
    content = content.encode("utf-8")
    content_len = len(content)
    if content_len == 0:
        return []
    
    chat_message = llama_cpp.llama_chat_message(role=role, content=content)
    buffer_length = content_len * 4 #2
    buffer = ctypes.create_string_buffer(buffer_length)
    result = llama_cpp.llama_chat_apply_template(model, chat_template, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result <= 0:
        print(f"Warning: model_tokenize_chat returned {result} for \"{content}\"")
    elif result >= buffer_length:
        buffer_length = result + 1
        buffer = ctypes.create_string_buffer(buffer_length)
        result = llama_cpp.llama_chat_apply_template(model, chat_template, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    content = buffer.value if result > 0 else content
    
    # Add space for llama only, check model params for add space var
    add_space = False # TODO: Check model/config for this
    if add_space:
        content = b" " + content
    
    # Tokenize
    content_len = len(content)
    content_len_c = ctypes.c_int32(content_len)
    tokens = (ctypes.c_int32 * content_len)()
    count = llama_cpp.llama_tokenize(model, content, content_len_c, tokens, content_len_c, True, True)
    if content_len > count:
        tokens = tokens[:count]
    return tokens

def print_tensor_info(t_ptr):
     #: contiguous: {ggml.ggml_is_contiguous(t)}, permuted: {ggml.ggml_is_permuted(t)}, transposed: {ggml.ggml_is_transposed(t)}"
    t = t_ptr.contents
    print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name}")
    print(f"  n_elements = {ggml.ggml_nelements(t)}")
    print(f"  ne         = ({t.ne[0]}, {t.ne[1]}, {t.ne[2]}, {t.ne[3]})")
    print(f"  nb         = ({t.nb[0]}, {t.nb[1]}, {t.nb[2]}, {t.nb[3]})")
    is_host = ggml.ggml_backend_buffer_is_host(t.buffer)
    print(f"  is_host    = {is_host}")
    print(f"  buffer     = {t.buffer}")
    print(f"  data       = {t.data}")
    if ctypes.c_void_p.from_buffer(t.src[0]).value != None:
        print(f"  src[0]     = {ggml.ggml_op_desc(t.src[0])}")
    if ctypes.c_void_p.from_buffer(t.src[1]).value != None:
        print(f"  src[1]     = {ggml.ggml_op_desc(t.src[1])}")

# Callback will fill this during model inference
class CallbackDataStruct(ctypes.Structure):
    _fields_ = [
        ("layer", ctypes.c_int),
        ("type", ctypes.c_int),
        ("buffer", ctypes.POINTER(ctypes.c_float))
    ]

callback_data = CallbackDataStruct()
callback_data.layer = 0
callback_data.type = 0

def hidden_states_eval_callback(t_void_p, ask, user_data):
    cb_data_ptr = ctypes.cast(user_data, ctypes.POINTER(CallbackDataStruct))
    cb_data = cb_data_ptr.contents
    t_ptr = ctypes.cast(t_void_p, ctypes.POINTER(ggml.ggml_tensor))
    t = t_ptr.contents
    if ask:
        name = t.name.decode("utf-8")
        match = re.match(r"inp_embd", name)
        if match:
            cb_data.type = 0
            cb_data.layer = 0
            return True
        match = re.match(r"kqv_out-(\d+)", name)
        if match:
            cb_data.type = 1
            cb_data.layer = int(match.group(1))
            return True
        match = re.match(r"ffn_out-(\d+)", name)
        if match:
            cb_data.type = 2
            cb_data.layer = int(match.group(1))
            return True
        return False
    else:
        offset = cb_data.layer if (cb_data.type == 0) else (cb_data.layer * 2 + 1) if (cb_data.type == 1) else (cb_data.layer * 2 + 2)
        data = ctypes.cast(t_ptr.contents.data, ctypes.POINTER(ctypes.c_float))
        dst_ptr = ctypes.c_void_p(ctypes.addressof(cb_data.buffer.contents) + (offset * t.ne[0]) * 4)
        ggml.ggml_backend_tensor_get(t_ptr, dst_ptr, (t.ne[0] * (t.ne[1]-1)) * 4, t.ne[0] * 4)
        # Returning false stops graph in it's tracks without error
        return True
    # return True to request data next callback, false to skip, ask will be False when returning data from a request
    return False

c_hidden_states_eval_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p, ctypes.c_bool, ctypes.c_void_p
)(hidden_states_eval_callback)

def model_generate_hidden_states(model, toks, buffer):
    # Set callback vars
    callback_data.buffer = buffer
    # Clear cache per sample instruction
    llama_cpp.llama_kv_cache_clear(context)
    # Token count
    n_tokens = len(toks)
    # Fill batch
    batch.n_tokens = n_tokens
    for i in range(n_tokens):
        batch.token[i] = toks[i]
        batch.pos[i] = i
        batch.seq_id[i][0] = 0
        batch.n_seq_id[i] = 1
        batch.logits[i] = False
    batch.logits[n_tokens - 1] = True
    # Decode batch
    result = llama_cpp.llama_decode(context, batch)
    if result == 1:
        print("decode warning")
    elif result < 0:
        print("decode error")

# Clear memory of past model usage
model = None
gc.collect()

# Load model
model = model_load(model_path)
n_embd = llama_cpp.llama_n_embd(model)

# Tokenize instructions
print("Instruction count: " + str(instructions))

dataset = load_dataset("byroneverson/abliterate-refusal", split="train")

# Filter the dataset based on 'target'
harmful_dataset = dataset.filter(lambda x: x['target'] == True)
harmless_dataset = dataset.filter(lambda x: x['target'] == False)

dataset = None
gc.collect()

# Randomly select 512 entries from each filtered dataset
harmful_instructions = random.sample(harmful_dataset['prompt'], instructions)
harmless_instructions = random.sample(harmless_dataset['prompt'], instructions)

harmful_dataset = None
harmless_dataset = None
gc.collect()

harmful_toks = [model_tokenize_chat(model, role="user", content=i, add_assistant=True) for i in harmful_instructions]
harmless_toks = [model_tokenize_chat(model, role="user", content=i, add_assistant=True) for i in harmless_instructions]

harmful_instructions = None
harmless_instructions = None
gc.collect()

# Create context and batch
def context_create(model, cb_eval, cb_eval_user_data):
    context_params = llama_cpp.llama_context_default_params()
    n_threads = multiprocessing.cpu_count()
    context_params.n_threads = n_threads
    context_params.n_threads_batch = n_threads
    context_params.seed  = 1337
    context_params.cb_eval = cb_eval
    context_params.cb_eval_user_data = ctypes.cast(ctypes.pointer(cb_eval_user_data), ctypes.c_void_p)
    context = llama_cpp.llama_new_context_with_model(model, context_params)
    batch = llama_cpp.llama_batch_init(context_params.n_batch, 0, context_params.n_ctx)
    return (context, batch)

context, batch = context_create(model, c_hidden_states_eval_callback, callback_data)

# Create ctypes float buffer
embedding_count = n_layers * 2 + 1
buffer_size = embedding_count * llama_cpp.llama_n_embd(model) * 4
buffer = ctypes.cast(ctypes.create_string_buffer(buffer_size), ctypes.POINTER(ctypes.c_float))

import time
sys.stdout.flush()
time.sleep(5) # Let model finish printing before start
sys.stdout.flush()

# Progress bar
max_its = instructions * 2
bar = tqdm(total=max_its)

# Generate target layer hidden state files for harmful and harmless features and save to file
def save_target_hidden_states(toks, index, feature, buffer):
    bar.update(n=1)
    model_generate_hidden_states(model, toks, buffer)
    # Convert float buffer to torch array for easy handling
    tensor = c_array_to_tensor(buffer, (embedding_count, n_embd), torch.float32)
    # Save tensor
    dir_path = working_dir + "/" + feature + "_states"
    file_path = dir_path + "/" + str(index) + ".pt"
    if not os.path.exists(dir_path):
        os.makedirs(dir_path)
    torch.save(tensor, file_path)

# Save harmful states
for index, toks in enumerate(harmful_toks):
    save_target_hidden_states(toks, index, "harmful", buffer)

# Save harmless states
for index, toks in enumerate(harmless_toks):
    save_target_hidden_states(toks, index, "harmless", buffer)

# End progress bar
bar.close()

# Free batch, model, context, and backend
llama_cpp.llama_batch_free(batch)
llama_cpp.llama_free(context)
llama_cpp.llama_free_model(model)
llama_cpp.llama_backend_free()

# Clean-up
harmful_toks = None
harmless_toks = None
callback_data = None
buffer = None
batch = None
model = None
context = None
gc.collect()


# Get refusal direction vector using my PCA (Primary Component Analysis) algorithm and save

This process is constantly evolving and attempting to write a decent description seems a little pointless.

In general, some form of PCA analysis is performed on the layers with the intent of seeing where in the model there is a large difference between harmful and harmless.

I basically with patching layers/tensors that have the most separation in the PCA analysis and keep adding layers until I have a good abliteration.

Another trick I used is increasing the "amount". 1.0 would simply remove the feature, but a value of 2.0 would effectively add the opposite of the feature. The opposite of refusal being something like submission. Extreme amounts like 5.0 - 10.0 will also increase intelligence degredation. 2.0 seems like a good amount, 6.0 helped with some prompts but interestingly enough, re-introduced refusal for others.

Based loosely on methods described here: https://www.lesswrong.com/posts/jGuXSZgv6qfdhMCuJ/refusal-in-llms-is-mediated-by-a-single-direction

In [1]:
%cd /kaggle/working

import torch
import math
import os
import gc
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

from bokeh.io import output_notebook
from bokeh.layouts import row, column
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, Slider, CustomJS
output_notebook()

working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Mistral-Small-Instruct-2409"
n_layers = 56
instructions = 512 #256 #32
n_components = 16 # PCA components


gc.collect()

# Load tensors
harmful_data = torch.stack([torch.load(f"{working_dir}/harmful_states/{i}.pt", weights_only=True) for i in range(instructions)])
harmless_data = torch.stack([torch.load(f"{working_dir}/harmless_states/{i}.pt", weights_only=True) for i in range(instructions)])

# Split by tensor type
harmful_tok = harmful_data[:, 0, :]
harmless_tok = harmless_data[:, 0, :]
harmful_attn = torch.cat((harmful_data[:, 0, :].unsqueeze(1), harmful_data[:, 1::2, :]), dim=1)
harmless_attn = torch.cat((harmless_data[:, 0, :].unsqueeze(1), harmless_data[:, 1::2, :]), dim=1)
harmful_ffn = harmful_data[:, ::2, :]
harmless_ffn = harmless_data[:, ::2, :]

# Instructions mean
#harmful_mean = harmful_data.mean(dim=0)
#harmless_mean = harmless_data.mean(dim=0)
harmful_mean_tok = harmful_tok.mean(dim=0)
harmless_mean_tok = harmless_tok.mean(dim=0)
harmful_mean_attn = harmful_attn.mean(dim=0)
harmless_mean_attn = harmless_attn.mean(dim=0)
harmful_mean_ffn = harmful_ffn.mean(dim=0)
harmless_mean_ffn = harmless_ffn.mean(dim=0)

# Feature mean diff
#mean_diff = harmful_mean - harmless_mean
mean_diff_tok = harmful_mean_tok - harmless_mean_tok
mean_diff_attn = harmful_mean_attn - harmless_mean_attn
mean_diff_ffn = harmful_mean_ffn - harmless_mean_ffn

def get_pca_plot(harmful_data, harmless_data, mean_diff, col_1, col_2):
    pca = PCA(n_components=64)
    layer_harmful = harmful_data[:, n_layers // 2, :]
    layer_harmless = harmless_data[:, n_layers // 2, :]
    pca.fit(torch.cat((layer_harmful, layer_harmless), 0))
    mean_diff_pca = torch.tensor(pca.transform(mean_diff))
    colors = [col_1, col_2] * (n_layers // 2)
    
    def get_pca_sub_plot(title, vals):
        mean_diff_source = ColumnDataSource(data={'x': [x for x in range(1, n_layers+1)], 'y': vals, 'c': colors})
        p = figure(width=600, height=200, title=title, x_range=(0, n_layers+1), y_range=(-1, 1))
        p.vbar(x='x', top='y', source=mean_diff_source, width=0.8, fill_color='c')
        p.xgrid.grid_line_color = None
        return p

    plot_prog = get_pca_sub_plot("mean diff progressive cos-sim", torch.cosine_similarity(mean_diff_pca[0:-1,:], mean_diff_pca[1:,:], dim=1))
    plot_mean = get_pca_sub_plot("mean diff mean cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca.mean(dim=0, keepdim=True), dim=1))
    plot_start = get_pca_sub_plot("mean diff start cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca[1,:].unsqueeze(0), dim=1))
    plot_end = get_pca_sub_plot("mean diff end cos-sim", torch.cosine_similarity(mean_diff_pca[1:,:], mean_diff_pca[-1,:].unsqueeze(0), dim=1))   
    return column(plot_prog, plot_mean, plot_start, plot_end)

# Show PCA of Attention
plot_attn = get_pca_plot(harmful_attn, harmless_attn, mean_diff_attn, "orange", "red")
# Show PCA of FFN
plot_ffn = get_pca_plot(harmful_ffn, harmless_ffn, mean_diff_ffn, "cyan", "blue")
# Show layout
show(row(plot_attn, plot_ffn))


'''

# New algorithm - "Oversampled PCA Reduction"
# TODO: Recycle z-score thresholding from previous scripts to trim outliers from samples (75% coverage) (64 -> 48 samples per part)
fig, ax = plt.subplots(nrows=4, ncols=3, figsize=(16, 3 * 4))

layer_scores = []

'''

# PCA
pca = PCA(n_components=n_components)

'''

#pc_harmful_inp = []
#pc_harmless_inp = []
pc_attn = []
#pc_harmless_attn = []
pc_ffn = []
#pc_harmless_ffn = []

#pca.fit(harmful_inp[:, :])
#pc_harmful_inp.append(torch.tensor(pca.components_))
#pca.fit(harmless_inp[:, :])
#pc_harmless_inp.append(torch.tensor(pca.components_))

'''

comp_harmful_attn = []
comp_harmless_attn = []
comp_harmful_ffn = []
comp_harmless_ffn = []

layer_harmful_attn = harmful_attn[:, n_layers // 2, :]
layer_harmless_attn = harmless_attn[:, n_layers // 2, :]
pca.fit(torch.cat((layer_harmful_attn, layer_harmless_attn), 0))
for layer in range(n_layers):
    layer_harmful_attn = harmful_attn[:, layer, :]
    layer_harmless_attn = harmless_attn[:, layer, :]
    #pca.fit(torch.cat((layer_harmful_attn, layer_harmless_attn), 0))
    #pc_attn.append(torch.tensor(pca.components_))
    comp_harmful_attn.append(torch.tensor(pca.transform(layer_harmful_attn)))
    comp_harmless_attn.append(torch.tensor(pca.transform(layer_harmless_attn)))
    #pca.fit(harmless_attn[:, layer, :])
    #pc_harmless_attn.append(torch.tensor(pca.components_))
    
layer_harmful_ffn = harmful_ffn[:, n_layers // 2, :]
layer_harmless_ffn = harmless_ffn[:, n_layers // 2, :]
pca.fit(torch.cat((layer_harmful_ffn, layer_harmless_ffn), 0))
for layer in range(n_layers):
    layer_harmful_ffn = harmful_ffn[:, layer, :]
    layer_harmless_ffn = harmless_ffn[:, layer, :]
    comp_harmful_ffn.append(torch.tensor(pca.transform(layer_harmful_ffn)))
    comp_harmless_ffn.append(torch.tensor(pca.transform(layer_harmless_ffn)))
    
# Stack layers to tensors
comp_harmful_attn = torch.stack(comp_harmful_attn, dim=1)
comp_harmless_attn = torch.stack(comp_harmless_attn, dim=1)
comp_harmful_ffn = torch.stack(comp_harmful_ffn, dim=1)
comp_harmless_ffn = torch.stack(comp_harmless_ffn, dim=1)

'''

layer_harmful_ffn = harmful_ffn[:, n_layers // 2, :]
layer_harmless_ffn = harmless_ffn[:, n_layers // 2, :]
pca.fit(torch.cat((layer_harmful_ffn, layer_harmless_ffn), 0))
for layer in range(n_layers):
    pc_ffn.append(torch.tensor(pca.components_))
    #pca.fit(harmless_ffn[:, layer, :])
    #pc_harmless_ffn.append(torch.tensor(pca.components_))

# Attn
# Cosine similarity of mean_diff and PCs
pc_attn = torch.stack(pc_attn, dim=1)
cos_sim_abs = torch.cosine_similarity(mean_attn_diff.unsqueeze(0), pc_attn, dim=-1).abs()
ax[0, 1].imshow(cos_sim_abs, cmap='BuGn', interpolation='nearest', vmin=0.0, vmax=1.0)
ax[0, 1].set_title("Cos-Sim Attn (Mean-Diff & PCs)")
# Get PC that correlates the most with mean_diff
cos_sim_abs_pc_sum = cos_sim_abs.sum(dim=-1)
cos_sim_abs_pc_sum_max = cos_sim_abs_pc_sum.argmax()
colors = ["blue"] * cos_sim_abs_pc_sum.shape[0]
colors[cos_sim_abs_pc_sum_max] = "green"
ax[1, 1].bar(x=range(cos_sim_abs_pc_sum.shape[0]), height=cos_sim_abs_pc_sum, color=colors)
ax[1, 1].set_title("Cos-Sim (Abs-Sum of PCs)")
# Get layer that correlates the most with mean_diff
cos_sim_abs_layer_sum = cos_sim_abs.sum(dim=0)
cos_sim_abs_layer_sum_max = cos_sim_abs_layer_sum.argmax()
colors = ["blue"] * cos_sim_abs_layer_sum.shape[0]
colors[cos_sim_abs_layer_sum_max] = "green"
ax[2, 1].bar(x=range(1, cos_sim_abs_layer_sum.shape[0] + 1), height=cos_sim_abs_layer_sum, color=colors)
ax[2, 1].set_title("Cos-Sim (Abs-Sum of Layers)")
#layer_scores.append(cos_sim_abs_layer_sum)

# FFN
# Cosine similarity of mean_diff and PCs
pc_ffn = torch.stack(pc_ffn, dim=1)
cos_sim_abs = torch.cosine_similarity(mean_ffn_diff.unsqueeze(0), pc_ffn, dim=-1).abs()
ax[0, 2].imshow(cos_sim_abs, cmap='BuGn', interpolation='nearest', vmin=0.0, vmax=1.0)
ax[0, 2].set_title("Cos-Sim FFN (Mean-Diff & PCs)")
# Get PC that correlates the most with mean_diff
cos_sim_abs_pc_sum = cos_sim_abs.sum(dim=-1)
cos_sim_abs_pc_sum_max = cos_sim_abs_pc_sum.argmax()
colors = ["blue"] * cos_sim_abs_pc_sum.shape[0]
colors[cos_sim_abs_pc_sum_max] = "green"
ax[1, 2].bar(x=range(cos_sim_abs_pc_sum.shape[0]), height=cos_sim_abs_pc_sum, color=colors)
ax[1, 2].set_title("Cos-Sim (Abs-Sum of PCs)")
# Get layer that correlates the most with mean_diff
cos_sim_abs_layer_sum = cos_sim_abs.sum(dim=0)
cos_sim_abs_layer_sum_max = cos_sim_abs_layer_sum.argmax()
colors = ["blue"] * cos_sim_abs_layer_sum.shape[0]
colors[cos_sim_abs_layer_sum_max] = "green"
ax[2, 2].bar(x=range(1, cos_sim_abs_layer_sum.shape[0] + 1), height=cos_sim_abs_layer_sum, color=colors)
ax[2, 2].set_title("Cos-Sim (Abs-Sum of Layers)")
#layer_scores.append(cos_sim_abs_layer_sum)
    
# Show partials plot
plt.tight_layout()
plt.show()

'''

# Show a PCA plot for PC 1 and 2, interpolates between layers
class PCAPlot:
    def __init__(self, title, width, height, comp_1, comp_2):
        # Group by layers via transpose so we can just set the offset for updating
        self.comp_1 = ColumnDataSource(data={'x': comp_1[:,:,0].transpose(0,1), 'y': comp_1[:,:,1].transpose(0,1)})
        self.comp_2 = ColumnDataSource(data={'x': comp_2[:,:,0].transpose(0,1), 'y': comp_2[:,:,1].transpose(0,1)})
        self.source_1 = ColumnDataSource(data={'x': self.comp_1.data['x'][0 * instructions : 1 * instructions], 'y': self.comp_1.data['y'][0 * instructions : 1 * instructions]})
        self.source_2 = ColumnDataSource(data={'x': self.comp_2.data['x'][0 * instructions : 1 * instructions], 'y': self.comp_2.data['y'][0 * instructions : 1 * instructions]})
        # Create the Bokeh figure
        self.plot = figure(title=title, width=width, height=height, x_axis_label='PC 1', y_axis_label='PC 2')
        self.plot.scatter('x', 'y', source=self.source_1, size=4, color='red', alpha=0.5)
        self.plot.scatter('x', 'y', source=self.source_2, size=4, color='blue', alpha=0.5)
        # Callback
        self.callback = CustomJS(args={'s1': self.source_1, 's2': self.source_2, 'c1': self.comp_1, 'c2': self.comp_2, 'n_layers': n_layers, 'n_ins': instructions}, code="""
            const val = cb_obj.value;
            if (1 <= val && val < n_layers) {
                const val_floor = Math.floor(val);
                const f = val - val_floor;
                const i = val_floor - 1;
                const x_f_1 = c1.data['x'].slice(i*n_ins,(i+1)*n_ins).map((element, index) => element*(1-f)+c1.data['x'].slice((i+1)*n_ins,(i+2)*n_ins)[index]*f);
                const y_f_1 = c1.data['y'].slice(i*n_ins,(i+1)*n_ins).map((element, index) => element*(1-f)+c1.data['y'].slice((i+1)*n_ins,(i+2)*n_ins)[index]*f);
                s1.data = {'x': x_f_1, 'y': y_f_1};
                const x_f_2 = c2.data['x'].slice(i*n_ins,(i+1)*n_ins).map((element, index) => element*(1-f)+c2.data['x'].slice((i+1)*n_ins,(i+2)*n_ins)[index]*f);
                const y_f_2 = c2.data['y'].slice(i*n_ins,(i+1)*n_ins).map((element, index) => element*(1-f)+c2.data['y'].slice((i+1)*n_ins,(i+2)*n_ins)[index]*f);
                s2.data = {'x': x_f_2, 'y': y_f_2};
            } else {
                s1.data = {'x': c1.data['x'].slice((n_layers-1)*n_ins,n_layers*n_ins), 'y': c1.data['y'].slice((n_layers-1)*n_ins,n_layers*n_ins)};
                s2.data = {'x': c2.data['x'].slice((n_layers-1)*n_ins,n_layers*n_ins), 'y': c2.data['y'].slice((n_layers-1)*n_ins,n_layers*n_ins)};
            }
            s1.change.emit();
            s2.change.emit();
        """)
        # Create slider and show
        self.slider = Slider(start=1, end=n_layers, value=1, step=0.1, title="Layer", width=width)
        self.slider.js_on_change('value', self.callback)

    def layout(self):
        return column(self.plot, self.slider)

# Show Attn PCA
plot_attn = PCAPlot("PCA: Attention", 600, 600, comp_harmful_attn, comp_harmless_attn)
plot_ffn = PCAPlot("PCA: FFN", 600, 600, comp_harmful_ffn, comp_harmless_ffn)
show(row(plot_attn.layout(), plot_ffn.layout())) #show(row(plot_attn.layout(), plot_ffn.layout()))

comp_harmful_attn = None
comp_harmless_attn = None
comp_harmful_ffn = None
comp_harmless_ffn = None
gc.collect()

'''

# Scores
#layer_scores = torch.stack(layer_scores, dim=0)
#scores = layer_scores.amax(dim=0)
# Get layer that correlates the most with mean_diff
#scores_max = scores.argmax()
#colors = ["blue"] * scores.shape[0]
#colors[scores_max] = "green"
#plt.figure(figsize=(12, 4))
#plt.bar(x=range(scores.shape[0]), height=scores, color=colors)
#plt.xlabel('Layer')
#plt.title('Scores (Max of partials)')
#plt.show()

# Delta scores
#delta = torch.cat((torch.tensor([0]), scores[1 :] - scores[ :-1]), dim=0)
#delta[ignore_first] = 0
#delta[n_layers - ignore_last + 1] = 0
#epsilon = 0.00000001
#delta = torch.maximum(delta / torch.maximum(scores, torch.tensor([epsilon] * scores.shape[0])), torch.zeros(delta.shape[0])) * 100.0
#delta_max = delta.argmax()
#colors = ["blue"] * delta.shape[0]
#colors[delta_max] = "green"
#plt.figure(figsize=(8, 4))
#plt.bar(x=range(delta.shape[0]), height=delta, color=colors)
#plt.xlabel('Layer')
#plt.title('Delta Scores (% Change)')
#plt.show()
                   
# Set layer_index to top scoring layer
#layer_index = 37 #scores_max #delta_max
#if layer_index == -1: # Fallback to 50% point
#    layer_index = n_layers // 2
#print(f"Using layer index: {layer_index}")

'''

# Save ideal layer mean_diff as refusal direction
#mean_inp_diff = -mean_inp_diff #[layer_index]
#mean_inp_diff_norm = mean_inp_diff / mean_inp_diff.norm(dim=0)
#mean_attn_diff = -mean_attn_diff #[layer_index]
#mean_attn_diff_norm = mean_attn_diff / mean_attn_diff.norm(dim=0)
#mean_ffn_diff = -mean_ffn_diff #[layer_index]
#mean_ffn_diff_norm = mean_ffn_diff / mean_ffn_diff.norm(dim=0)
#refusal_direction = torch.cat((mean_inp_diff_norm.unsqueeze(0), mean_attn_diff_norm, mean_ffn_diff_norm), 0)
#print(refusal_direction.shape)
#layer = 29
#layer_index = 1 + 2 * layer

# Directions path
if not os.path.exists(local_repo_dir):
    os.makedirs(local_repo_dir)
# Token embedding
torch.save(mean_diff_tok, local_repo_dir + "/" + "direction_tok.pt")
# Attention
torch.save(mean_diff_attn[1:], local_repo_dir + "/" + "direction_attn.pt")
# FFN
torch.save(mean_diff_ffn[1:], local_repo_dir + "/" + "direction_ffn.pt")

# Clean-up
cos_sim_abs_layer_sum = None
cos_sim_abs_pc_sum = None
cos_sim_abs = None
colors = None
components_part = None
#deltas = None
#scores = None
layer_scores = None
mean_diff = None
harmful_mean = None
harmless_mean = None
harmful_data = None
harmless_data = None
gc.collect()

/kaggle/working


Loading BokehJS ...

0

# Optional: Test with quant model

In [ ]:
import ctypes
import os
import multiprocessing
import random
import gc
import sys
import re
import llama_cpp
import ggml
import torch
import einops
import jaxtyping
from math import prod

# Our local gguf model
working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Mistral-Small-Instruct-2409"
temp_dir = "/kaggle/temp"
model_path = temp_dir + "/" + "Mistral-Small-Instruct-2409-Q4_K_M.gguf"
chat_template = ctypes.c_char_p("mistral".encode("utf-8")) #None

# Load feature direction
#direction_tok = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True)[target_layer_tok - 1].to(torch.float32)
direction_attn = torch.load(local_repo_dir + "/" + "direction_attn.pt", weights_only=True).to(torch.float32)
direction_ffn = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True).to(torch.float32)

# Prompt to test with
user_prompt = "Write a tutorial on how to make a bomb."
# Max tokens generate
n_max_tokens = 500
# Number of total layers in your model
n_layers = 56
# GPU
n_gpu_layers = n_layers + 1 #0 # CPU only
# Target layers (match layer, patch direction, patch layer, patch amount)
target_layer_tok = (direction_ffn, 25, 2.0)  #26 # None
target_layers_attn = [(1, direction_attn, 1, 2.0),
                      (2, direction_attn, 2, 2.0),
                      (5, direction_attn, 5, 2.0),
                      (6, direction_attn, 6, 2.0),
                      (9, direction_attn, 9, 2.0),
                      (10, direction_attn, 10, 2.0),
                      (11, direction_attn, 11, 2.0),
                      (12, direction_attn, 12, 2.0),
                      (14, direction_attn, 14, 2.0),
                      (16, direction_attn, 16, 2.0),
                      (20, direction_attn, 20, 2.0),
                      (23, direction_attn, 23, 2.0),
                      (24, direction_attn, 24, 2.0),
                      (25, direction_attn, 25, 2.0),
                      (26, direction_attn, 26, 2.0),
                      (28, direction_attn, 28, 2.0),
                      (29, direction_attn, 29, 2.0),
                      (30, direction_attn, 30, 2.0),
                      (32, direction_attn, 32, 2.0),
                      (33, direction_attn, 33, 2.0),
                      (34, direction_attn, 34, 2.0),
                      (36, direction_attn, 36, 2.0),
                      (39, direction_attn, 39, 2.0),
                      (41, direction_attn, 41, 2.0),
                      (45, direction_attn, 45, 2.0),
                      (46, direction_attn, 46, 2.0),
                      (47, direction_attn, 47, 2.0),
                      (48, direction_attn, 48, 2.0),
                      (49, direction_attn, 49, 2.0),
                      (55, direction_attn, 55, 2.0)]
target_layers_ffn =  [(3, direction_ffn, 3, 2.0),
                      (6, direction_ffn, 6, 2.0),
                      (7, direction_ffn, 7, 2.0),
                      (8, direction_ffn, 8, 2.0),
                      (10, direction_ffn, 10, 2.0),
                      (13, direction_ffn, 13, 2.0),
                      (14, direction_ffn, 14, 2.0),
                      (15, direction_ffn, 15, 2.0),
                      (16, direction_ffn, 16, 2.0),
                      (17, direction_ffn, 17, 2.0),
                      (19, direction_ffn, 19, 2.0),
                      (21, direction_ffn, 21, 2.0),
                      (23, direction_ffn, 23, 2.0),
                      (24, direction_ffn, 24, 2.0),
                      (25, direction_ffn, 25, 2.0),
                      (28, direction_ffn, 28, 2.0),
                      (29, direction_ffn, 29, 2.0),
                      (30, direction_ffn, 30, 2.0),
                      (32, direction_ffn, 32, 2.0),
                      (33, direction_ffn, 33, 2.0),
                      (35, direction_ffn, 35, 2.0),
                      (37, direction_ffn, 37, 2.0),
                      (38, direction_ffn, 38, 2.0),
                      (40, direction_ffn, 40, 2.0),
                      (41, direction_ffn, 41, 2.0),
                      (43, direction_ffn, 43, 2.0),
                      (45, direction_ffn, 45, 2.0),
                      (48, direction_ffn, 48, 2.0),
                      (51, direction_ffn, 51, 2.0),
                      (52, direction_ffn, 52, 2.0),
                      (53, direction_ffn, 53, 2.0),
                      (54, direction_ffn, 54, 2.0)]

# Init llama backend
llama_cpp.llama_backend_init(numa=False)

# llama.cpp custom model code

def orthogonalize_matrix(matrix: jaxtyping.Float[torch.Tensor, "... d"], 
                        direction: jaxtyping.Float[torch.Tensor, "d"],
                        amount: float = 1.0) -> jaxtyping.Float[torch.Tensor, "... d"]:
    proj = einops.einsum(matrix, direction.view(-1, 1), "... d, d single -> ... single") * direction * amount
    return matrix - proj

def c_array_to_tensor(pointer, shape, torch_type):
    arr = (pointer._type_ * prod(shape)).from_address(
    ctypes.addressof(pointer.contents))
    return torch.frombuffer(arr, dtype=torch_type).view(*shape)

def model_load(model_path):
    # TODO: Attempt to hook num_layers
    model_params = llama_cpp.llama_model_default_params()
    model_params.n_gpu_layers = n_gpu_layers
    model_params.use_mmap = True
    model = llama_cpp.llama_load_model_from_file(model_path.encode("utf-8"), model_params)
    return model

def model_free(model):
    llama_cpp.llama_free(model)
    
def model_tokenize_chat(model, role, content, add_assistant=True):
    role = role.encode("utf-8")
    content = content.encode("utf-8")
    content_len = len(content)
    if content_len == 0:
        return []
    
    chat_message = llama_cpp.llama_chat_message(role=role, content=content)
    buffer_length = content_len * 2
    buffer = ctypes.create_string_buffer(buffer_length)
    result = llama_cpp.llama_chat_apply_template(model, chat_template, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    if result <= 0:
        print(f"Warning: model_tokenize_chat returned {result} for \"{content}\"")
    elif result >= buffer_length:
        buffer_length = result + 1
        buffer = ctypes.create_string_buffer(buffer_length)
        result = llama_cpp.llama_chat_apply_template(model, chat_template, ctypes.pointer(chat_message), 1, add_assistant, buffer, ctypes.c_int32(buffer_length))
    content = buffer.value if result > 0 else content
    
    # Add space for llama only, check model params for add space var
    add_space = False # TODO: Check model/config for this, not used for gemma 2
    if add_space:
        content = b" " + content
    
    # Tokenize
    content_len = len(content)
    content_len_c = ctypes.c_int32(content_len)
    tokens = (ctypes.c_int32 * content_len)()
    count = llama_cpp.llama_tokenize(model, content, content_len_c, tokens, content_len_c, True, True)
    if content_len > count:
        tokens = tokens[:count]
    return tokens

def print_tensor_info(t_ptr):
     #: contiguous: {ggml.ggml_is_contiguous(t)}, permuted: {ggml.ggml_is_permuted(t)}, transposed: {ggml.ggml_is_transposed(t)}"
    t = t_ptr.contents
    print(f"{ggml.ggml_type_name(t.type)} {ggml.ggml_op_desc(t_ptr)} {t.name}")
    print(f"  n_elements = {ggml.ggml_nelements(t)}")
    print(f"  ne         = ({t.ne[0]}, {t.ne[1]}, {t.ne[2]}, {t.ne[3]})")
    print(f"  nb         = ({t.nb[0]}, {t.nb[1]}, {t.nb[2]}, {t.nb[3]})")
    is_host = ggml.ggml_backend_buffer_is_host(t.buffer)
    print(f"  is_host    = {is_host}")
    print(f"  buffer     = {t.buffer}")
    print(f"  data       = {t.data}")
    if ctypes.c_void_p.from_buffer(t.src[0]).value != None:
        print(f"  src[0]     = {ggml.ggml_op_desc(t.src[0])}")
    if ctypes.c_void_p.from_buffer(t.src[1]).value != None:
        print(f"  src[1]     = {ggml.ggml_op_desc(t.src[1])}")

# Callback will fill this during model inference
class CallbackDataStruct(ctypes.Structure):
    _fields_ = [
        ("type", ctypes.c_int),
        ("layer", ctypes.c_int),
        ("buffer", ctypes.POINTER(ctypes.c_float)) #,
        #("direction", ctypes.POINTER(ctypes.c_float))
    ]

callback_data = CallbackDataStruct()
callback_data.type = 0
callback_data.layer = 0

def hidden_states_eval_callback(t_void_p, ask, user_data):
    cb_data_ptr = ctypes.cast(user_data, ctypes.POINTER(CallbackDataStruct))
    cb_data = cb_data_ptr.contents
    t_ptr = ctypes.cast(t_void_p, ctypes.POINTER(ggml.ggml_tensor))
    t = t_ptr.contents
    if ask:
        name = t.name.decode("utf-8")
        did_match = False
        if match := re.match(r"inp_embd", name):
            cb_data.type = 0
            cb_data.layer = 0
            return (target_layer_tok is not None)
        elif match := re.match(r"kqv_out-(\d+)", name):
            cb_data.type = 1
            cb_data.layer = int(match.group(1)) + 1
            return any(layer == cb_data.layer for layer, _, _, _ in target_layers_attn)
        elif match := re.match(r"ffn_out-(\d+)", name):
            cb_data.type = 2
            cb_data.layer = int(match.group(1)) + 1
            return any(layer == cb_data.layer for layer, _, _, _ in target_layers_ffn)
        return False
    else:
        # Get tensor data
        buffer_ptr = ctypes.cast(cb_data.buffer, ctypes.c_void_p)
        ggml.ggml_backend_tensor_get(t_ptr, buffer_ptr, 0, t.ne[0] * 4)
        tensor = c_array_to_tensor(cb_data.buffer, (1, t.ne[0]), torch.float32)
        # Orthogonalize with correct direction
        if cb_data.type == 0:
            direction, layer, amount = target_layer_tok
            tensor = orthogonalize_matrix(tensor, direction[layer - 1], amount)
        if cb_data.type == 1:
            for match, direction, layer, amount in target_layers_attn:
                if match == cb_data.layer:
                    tensor = orthogonalize_matrix(tensor, direction[layer - 1], amount)
                    break
        if cb_data.type == 2:
            for match, direction, layer, amount in target_layers_ffn:
                if match == cb_data.layer:
                    tensor = orthogonalize_matrix(tensor, direction[layer - 1], amount)
                    break
        # Set tensor data
        ggml.ggml_backend_tensor_set(t_ptr, tensor.numpy().ctypes.data, 0, t.ne[0] * 4)
        # Returning false stops graph in it's tracks without error
        return True
    # return True to request data next callback, false to skip, ask will be False when returning data from a request
    return False

c_hidden_states_eval_callback = ctypes.CFUNCTYPE(
    ctypes.c_bool, ctypes.c_void_p, ctypes.c_bool, ctypes.c_void_p
)(hidden_states_eval_callback)

def model_generate_hidden_states(model, context, batch, n_past, toks, buffer): #, direction):
    # Set callback vars
    callback_data.buffer = buffer
    #callback_data.direction = direction
    # Clear cache per sample instruction
    #llama_cpp.llama_kv_cache_clear(context)
    # Token count
    n_tokens = len(toks)
    # Fill batch
    batch.n_tokens = n_tokens
    for i in range(n_tokens):
        batch.token[i] = toks[i]
        batch.pos[i] = n_past + i
        batch.seq_id[i][0] = 0
        batch.n_seq_id[i] = 1
        batch.logits[i] = False
    batch.logits[n_tokens - 1] = True
    # Decode batch
    result = llama_cpp.llama_decode(context, batch)
    if result == 1:
        print("decode warning")
    elif result < 0:
        print("decode error")

def model_token_to_piece(model, token) -> str:
    size = 32
    buffer = (ctypes.c_char * size)()
    n = llama_cpp.llama_token_to_piece(model, llama_cpp.llama_token(token), buffer, size, 0, True)
    return buffer[:n].decode("utf-8")

# Clear memory of past model usage
model = None
gc.collect()

# Load model
model = model_load(model_path)
n_embd = llama_cpp.llama_n_embd(model)

toks = model_tokenize_chat(model, role="user", content=user_prompt, add_assistant=True)

#toks = [toks[0]]

# Create context and batch
def context_create(model, cb_eval, cb_eval_user_data):
    context_params = llama_cpp.llama_context_default_params()
    n_threads = multiprocessing.cpu_count()
    context_params.n_threads = n_threads
    context_params.n_threads_batch = n_threads
    context_params.seed  = 1337
    context_params.cb_eval = cb_eval
    context_params.cb_eval_user_data = ctypes.cast(ctypes.pointer(cb_eval_user_data), ctypes.c_void_p)
    context = llama_cpp.llama_new_context_with_model(model, context_params)
    batch = llama_cpp.llama_batch_init(context_params.n_batch, 0, context_params.n_ctx)
    return (context, batch)

context, batch = context_create(model, c_hidden_states_eval_callback, callback_data)

# Create ctypes float direction
buffer_n_bytes = llama_cpp.llama_n_embd(model) * 4
buffer = ctypes.cast(ctypes.create_string_buffer(buffer_n_bytes), ctypes.POINTER(ctypes.c_float))

# Generate response
# Input tokens
n_past = 0
n_toks = len(toks)
for tok in toks:
    print(model_token_to_piece(model, tok), end="", flush=True)
    model_generate_hidden_states(model, context, batch, n_past, [tok], buffer)
    n_past += 1
# Output tokens (simple greedy)
n_generated = 0
is_generating = True
while is_generating:
    # Sample token
    logits = llama_cpp.llama_get_logits(context)
    n_vocab = llama_cpp.llama_n_vocab(model)
    data_array = (llama_cpp.llama_token_data * n_vocab)(
        *[llama_cpp.llama_token_data(token_id, logits[token_id], 0.0) for token_id in range(n_vocab)]
    )
    candidates = ctypes.pointer(llama_cpp.llama_token_data_array(data_array, len(data_array), False))
    probs = llama_cpp.llama_sample_softmax(context, candidates)
    tok = llama_cpp.llama_sample_token_greedy(context, candidates)
    # Check for stop tokens
    if llama_cpp.llama_token_is_eog(model, tok):
        is_generating = False
        break
    # Print token and generate another if needed
    print(model_token_to_piece(model, tok), end="", flush=True)
    n_generated += 1
    if n_generated >= n_max_tokens:
        is_generating = False
        break
    model_generate_hidden_states(model, context, batch, n_past, [tok], buffer)
    n_past += 1

# Free batch, model, context, and backend
llama_cpp.llama_batch_free(batch)
llama_cpp.llama_free(context)
llama_cpp.llama_free_model(model)
llama_cpp.llama_backend_free()

# Clean-up
toks = None
callback_data = None
buffer = None
batch = None
model = None
context = None
gc.collect()

# Optional: Remove temporary harmful and harmless hidden state files

In [ ]:
#%cd /kaggle/working
#!rm -r ./harmful_states
#!rm -r ./harmless_states

# Download/modify/upload individual safetensors files separately to save memory

To save space in kaggle, I will download each split separately and patch it, then upload it to my own repo.

All of the smaller files will be uploaded as a folder.

Be sure to change the repo to your newly created huggingface repo and set all your kaggle secrets for reading and writing to hf!

There is some basic code to check and resume progress if something fails during the process. Not perfect, but helpful.

In [1]:
# Run this command only if you need to reset the upload progress!
!rm /kaggle/working/upload_progress.pt

In [ ]:
%cd /kaggle/working

import os
import re
import gc
gc.collect()

from safetensors import safe_open
from safetensors.torch import save_file
from typing import Optional, Tuple

import einops
import jaxtyping
import torch

from huggingface_hub import hf_hub_download
from huggingface_hub import upload_folder
from huggingface_hub import upload_file

from transformers import AutoConfig

working_dir = "/kaggle/working"
local_repo_dir = working_dir + "/" + "Mistral-Small-Instruct-2409"

download_repo = "mistralai/Mistral-Small-Instruct-2409"
upload_repo = "byroneverson/Mistral-Small-Instruct-2409-abliterated"

temp_dir = "/kaggle/temp"

# Make sure safetensors count matches the actual count for the model you are modifying
safetensors_count = 9

# Load feature direction
#direction_tok = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True)[target_layer_tok - 1].to(torch.float32)
direction_attn = torch.load(local_repo_dir + "/" + "direction_attn.pt", weights_only=True).to(torch.float32)
direction_ffn = torch.load(local_repo_dir + "/" + "direction_ffn.pt", weights_only=True).to(torch.float32)

# Target layers
target_layer_tok = (direction_ffn, 25, 2.0)  #26 # None
target_layers_attn = [(1, direction_attn, 1, 2.0),
                      (2, direction_attn, 2, 2.0),
                      (5, direction_attn, 5, 2.0),
                      (6, direction_attn, 6, 2.0),
                      (9, direction_attn, 9, 2.0),
                      (10, direction_attn, 10, 2.0),
                      (11, direction_attn, 11, 2.0),
                      (12, direction_attn, 12, 2.0),
                      (14, direction_attn, 14, 2.0),
                      (16, direction_attn, 16, 2.0),
                      (20, direction_attn, 20, 2.0),
                      (23, direction_attn, 23, 2.0),
                      (24, direction_attn, 24, 2.0),
                      (25, direction_attn, 25, 2.0),
                      (26, direction_attn, 26, 2.0),
                      (28, direction_attn, 28, 2.0),
                      (29, direction_attn, 29, 2.0),
                      (30, direction_attn, 30, 2.0),
                      (32, direction_attn, 32, 2.0),
                      (33, direction_attn, 33, 2.0),
                      (34, direction_attn, 34, 2.0),
                      (36, direction_attn, 36, 2.0),
                      (39, direction_attn, 39, 2.0),
                      (41, direction_attn, 41, 2.0),
                      (45, direction_attn, 45, 2.0),
                      (46, direction_attn, 46, 2.0),
                      (47, direction_attn, 47, 2.0),
                      (48, direction_attn, 48, 2.0),
                      (49, direction_attn, 49, 2.0),
                      (55, direction_attn, 55, 2.0)]
target_layers_ffn =  [(3, direction_ffn, 3, 2.0),
                      (6, direction_ffn, 6, 2.0),
                      (7, direction_ffn, 7, 2.0),
                      (8, direction_ffn, 8, 2.0),
                      (10, direction_ffn, 10, 2.0),
                      (13, direction_ffn, 13, 2.0),
                      (14, direction_ffn, 14, 2.0),
                      (15, direction_ffn, 15, 2.0),
                      (16, direction_ffn, 16, 2.0),
                      (17, direction_ffn, 17, 2.0),
                      (19, direction_ffn, 19, 2.0),
                      (21, direction_ffn, 21, 2.0),
                      (23, direction_ffn, 23, 2.0),
                      (24, direction_ffn, 24, 2.0),
                      (25, direction_ffn, 25, 2.0),
                      (28, direction_ffn, 28, 2.0),
                      (29, direction_ffn, 29, 2.0),
                      (30, direction_ffn, 30, 2.0),
                      (32, direction_ffn, 32, 2.0),
                      (33, direction_ffn, 33, 2.0),
                      (35, direction_ffn, 35, 2.0),
                      (37, direction_ffn, 37, 2.0),
                      (38, direction_ffn, 38, 2.0),
                      (40, direction_ffn, 40, 2.0),
                      (41, direction_ffn, 41, 2.0),
                      (43, direction_ffn, 43, 2.0),
                      (45, direction_ffn, 45, 2.0),
                      (48, direction_ffn, 48, 2.0),
                      (51, direction_ffn, 51, 2.0),
                      (52, direction_ffn, 52, 2.0),
                      (53, direction_ffn, 53, 2.0),
                      (54, direction_ffn, 54, 2.0)]

# Use kaggle secrets to store HF read/write tokens
# Ensure you have these kaggle secrets setup for this notebook or simply paste your read/write tokens here from HF
from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
read_token = user_secrets.get_secret("hf_read")
write_token = user_secrets.get_secret("hf_write")

# Download necessary non-weights files
try:
    for filename in ["config.json", 
                     "generation_config.json",
                     "model.safetensors.index.json", 
                     "special_tokens_map.json", 
                     "tokenizer.json", 
                     "tokenizer.model", 
                     "tokenizer.model.v3", 
                     "tokenizer_config.json",
                     "params.json"]:
        hf_hub_download(repo_id=download_repo, filename=filename, local_dir=local_repo_dir, use_auth_token=read_token)
except Exception as e:
    print(f"Error downloading {filename}: {e}")

# Upload smaller files first
try:
    upload_folder(folder_path=local_repo_dir, repo_id=upload_repo, token=write_token)
except Exception as e:
    print(f"Error uploading folder: {e}")

# Load model config and refusal direction
config = AutoConfig.from_pretrained(local_repo_dir, local_files_only=True, trust_remote_code=True)

def orthogonalize_matrix(matrix: jaxtyping.Float[torch.Tensor, "... d"], 
                        direction: jaxtyping.Float[torch.Tensor, "d"],
                        amount: float = 1.0) -> jaxtyping.Float[torch.Tensor, "... d"]:
    proj = einops.einsum(matrix, direction.view(-1, 1), "... d, d single -> ... single") * direction * amount
    return matrix - proj

def load_safetensors_file(file_path):
    """Loads a single safetensors file into a dictionary of tensors.
    Args:
        file_path (str): Path to the safetensors file.
    Returns:
        dict: A dictionary containing the loaded tensors.
    """
    tensors = {}
    with safe_open(file_path, framework="pt", device="cpu") as f:
        #print(f.metadata())
        for key in f.keys():
            tensors[key] = f.get_tensor(key)
    return tensors

# Check for upload progress, if none create one
progress = None
progress_filename = "/kaggle/working/upload_progress.pt"
if os.path.isfile(progress_filename):
    progress = torch.load(progress_filename, weights_only=True)
else:
    progress = torch.tensor([0, 0])
    torch.save(progress, progress_filename)

start_index = progress[0]
device = direction_ffn.device
# TODO: Add in skip start and end layers logic
#       I forgot to in v1.0 but the abliterated output model still worked great so I didn't even notice
for idx in range(start_index, safetensors_count):
    gc.collect()
    
    # Current .safetensors
    filename = "model-" + str(idx + 1).zfill(5) + "-of-" + str(safetensors_count).zfill(5) + ".safetensors"
    print(filename)
    
    # Local file path
    file_path = temp_dir + "/" + filename
    
    # Check if we need to skip processing this file and just upload it
    skip_processing = False
    
    # Download file 
    if os.path.isfile(file_path):
        skip_processing = True if progress[1] >= 1 else False
    else:
        hf_hub_download(repo_id=download_repo, filename=filename, local_dir=temp_dir, use_auth_token=read_token)
    
    if not skip_processing:
        # Load local file
        tensors = load_safetensors_file(file_path)

        for tensor in tensors:
            
            # Get current layer number (not layer index)
            tensor_layer = -1
            match = re.search(r"layers\.(\d+)\.", tensor)
            if match:
                tensor_layer = int(match.group(1)) + 1

            # tok_embeddings
            if ".embed_tokens.weight" in tensor:
                if target_layer_tok:
                    direction, layer, amount = target_layer_tok
                    print("• " + tensor)
                    dtype = tensors[tensor].dtype
                    t = tensors[tensor].to(torch.float32).to(device)
                    tensors[tensor].copy_(orthogonalize_matrix(t, direction[layer - 1], amount).to(dtype))
                    t = []

            # attention.wo
            if ".self_attn.o_proj.weight" in tensor:
                for match, direction, layer, amount in target_layers_attn:
                    if match == tensor_layer:
                        print("• " + tensor)
                        dtype = tensors[tensor].dtype
                        t = tensors[tensor].to(torch.float32).to(device)
                        t_rearranged = einops.rearrange(t, "m (n h) -> n h m", n=config.num_attention_heads).to(device)
                        t_orthogonalized = orthogonalize_matrix(t_rearranged, direction[layer - 1], amount)
                        t_rearranged = einops.rearrange(t_orthogonalized, "n h m -> m (n h)", n=config.num_attention_heads)
                        tensors[tensor].copy_(t_rearranged.to(dtype))
                        t = []
                        t_rearranged = []
                        t_orthogonalized = []

            # feed_forward.w2
            if ".mlp.down_proj.weight" in tensor:
                for match, direction, layer, amount in target_layers_ffn:
                    if match == tensor_layer:
                        print("• " + tensor)
                        dtype = tensors[tensor].dtype
                        t = tensors[tensor].to(torch.float32).to(device)
                        t_transposed = t.T.to(device)
                        t_orthogonalized = orthogonalize_matrix(t_transposed, direction[layer - 1], amount)
                        t_transposed = t_orthogonalized.T
                        tensors[tensor].copy_(t_transposed.to(dtype))
                        t = []
                        t_transposed = []
                        t_orthogonalized = []

        # Save file
        save_file(tensors, file_path, metadata={'format': 'pt'})

        # Save progress after processing
        progress[1] = 1
        torch.save(progress, progress_filename)
        
    # Upload file if we need to
    skip_upload = True if progress[1] >= 2 else False
    if not skip_upload:
        # Upload file to your repo
        upload_file(path_or_fileobj=file_path, path_in_repo=filename, repo_id=upload_repo, token=write_token)
        
        # Save progress after processing
        progress[1] = 2
        torch.save(progress, progress_filename)

    # Try to remove file if it still exists
    import os
    if os.path.exists(file_path):
        os.remove(file_path)
    else:
        print("Remove error: The file does not exist")
        
    # Save progress for next file
    progress[0] = idx + 1
    progress[1] = 0
    torch.save(progress, progress_filename)

# Delete progress file
!rm /kaggle/working/upload_progress.pt

# Patching done
print("Done!")


# Use GGUF My Repo space on HF to convert abliterated model to GGUF

# Test in your favorite llama.cpp or GGUF environment